In [1]:
import torch
import torchvision
from torchvision import datasets

In [2]:
import os
import numpy as np
import tensorflow as tf
import trainer_2d
import data_utils

In [3]:
import matplotlib.pyplot as plt
import pandas as pd
from tqdm import tqdm

In [4]:
import importlib
importlib.reload(trainer_2d)
importlib.reload(data_utils)

<module 'data_utils' from '/Users/nastya/Documents/ucu/thesis/diffeomorphic_demons/src/data_utils.py'>

Process data

In [5]:
import pickle

with open('/Users/nastya/Documents/ucu/thesis/data/mnist_split/test_mnist.pkl', "rb") as f:
    test_set = pickle.load(f)

In [6]:
test_set = [(data_utils.convert_to_uint(pair[1], 127), data_utils.convert_to_uint(pair[0], 127)) for pair in test_set]

Metrics dataframe

In [7]:
metrics_data = pd.DataFrame(columns=['image_pair', 'mse', 'dice'])

Demons

In [8]:
model_path = '/Users/nastya/Documents/ucu/thesis/diffeomorphic_demons/src/mnist/model'
general_prediction_path = '/Users/nastya/Documents/ucu/thesis/diffeomorphic_demons/src/mnist/predictions'

for idx, (source_image, target_image) in tqdm(enumerate(test_set)):

    prediction_path = os.path.join(general_prediction_path, f'pair_{idx}')

    source_image = trainer_2d._load_data_from_array(source_image)
    target_image = trainer_2d._load_data_from_array(target_image)
    
    source_label = trainer_2d._one_hot_label(source_image, labels=(0, 255))
    target_label = trainer_2d._one_hot_label(target_image, labels=(0, 255))

    training_data = {'target_image': target_image, 'target_label': target_label,
                 'source_image': source_image, 'source_label': source_label,
                 'target_affine': np.eye(4), 'target_header': None
                 }

    
    with tf.Graph().as_default(), tf.device('/cpu:0'):
        trainer = trainer_2d.Trainer(input_size=(source_image.shape[1], source_image.shape[2]), num_channels=1, num_classes=2,
                          demons_type='diffeomorphic', demons_force='moving', normalization='z-score',
                          max_length=2., exp_steps=7)

        metrics, save_path = trainer.train(training_data, training_iters=100,
                                           display_steps=0,
                                           model_path=model_path,
                                           prediction_path=prediction_path)

        new_row = {'image_pair': idx, 'mse': trainer.final_mse, 'dice': trainer.final_dice}
        metrics_data.loc[len(metrics_data)] = new_row

0it [00:00, ?it/s]

Instructions for updating:
Use fn_output_signature instead


2024-04-25 14:57:48,155 From /opt/homebrew/lib/python3.9/site-packages/tensorflow/python/util/deprecation.py:660: calling map_fn_v2 (from tensorflow.python.ops.map_fn) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Use fn_output_signature instead
2024-04-25 14:57:49,185 Removing '/Users/nastya/Documents/ucu/thesis/diffeomorphic_demons/src/mnist/predictions/pair_0'
2024-04-25 14:57:49,188 Removing '/Users/nastya/Documents/ucu/thesis/diffeomorphic_demons/src/mnist/model'
2024-04-25 14:57:49,191 Allocating '/Users/nastya/Documents/ucu/thesis/diffeomorphic_demons/src/mnist/predictions/pair_0'
2024-04-25 14:57:49,191 Allocating '/Users/nastya/Documents/ucu/thesis/diffeomorphic_demons/src/mnist/model'
2024-04-25 14:57:49.207104: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:388] MLIR V1 optimization pass is not enabled
2024-04-25 14:57:49,305 Start optimization with demons configuration: demons force: moving, demons type: diffeomorph

In [9]:
metrics_data.head(3)

image_pair       mse      dice
0           0  0.008517  0.959538
1           1  0.004329  0.969325
2           2  0.007571  0.979424

In [11]:
mean_mse = metrics_data.loc[:, 'mse'].mean()
mean_mse

0.020947631

In [12]:
mean_dice = metrics_data.loc[:, 'dice'].mean()
mean_dice

0.89124525

In [13]:
metrics_data.to_csv('/Users/nastya/Documents/ucu/thesis/diffeomorphic_demons/src/mnist/metrics.csv')